# Predict the year from the abstract 

In [1]:
import pandas as pd
import numpy as np
import pickle
import matplotlib.pyplot as plt
from tqdm.notebook import tqdm
import time

import string # библиотека для работы со строками
import nltk   # Natural Language Toolkit
# загружаем библиотеку для лемматизации
import pymorphy2 # Морфологический анализатор

#вычисляем tf-idf
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.preprocessing import Binarizer

In [174]:
from data_types import AuthorsDB
from data_types import PublicationsDB
from data_types import AbstractsDB

audb = AuthorsDB()
audb.load()
pubdb = PublicationsDB()
pubdb.load()
absdb = AbstractsDB()
absdb.load()

filename = "../data/mnid_author_dict.pkl"
with open(filename,'rb') as inp:
    authors_dict = pickle.load(inp)

In [169]:
# authors_dict2 = {v['mn_id']:v['name'] for k,v in authors_dict.items()}

In [175]:
ind = 0
for k, v in authors_dict.items():
    ind += 1
    print(k,v)
    if ind>4:
        break
        

29400 Абалакин Илья Владимирович
25875 Авдуевский Всеволод Сергеевич
79709 Агапов Владимир Михайлович
37981 Агафонов С И
39797 Агаян В М


In [172]:
# filename = '../data/mnid_author_dict.pkl'    
# with open(filename,'wb') as outp:
#     pickle.dump(authors_dict2, outp, pickle.HIGHEST_PROTOCOL)

In [ ]:
# filename = "../data/mathnet_iam_authors_dict.pkl"
# with open(filename,'rb') as inp:
#     authors_dict = pickle.load(inp)

In [3]:
pub = pd.DataFrame.from_dict(pubdb.db,orient='index')

# 1 Data Preprocessing

I need to get 
- abstract and it's tokenization
- year of paper



In [4]:
abstracts = absdb.db[absdb.db['abstract'].notna()].copy()

In [5]:
absdb.db.info()

<class 'pandas.core.frame.DataFrame'>
Index: 7597 entries, vyurv213 to vmumm4420
Data columns (total 2 columns):
 #   Column    Non-Null Count  Dtype 
---  ------    --------------  ----- 
 0   abstract  5609 non-null   object
 1   keywords  2525 non-null   object
dtypes: object(2)
memory usage: 178.1+ KB


In [6]:
abstracts.info()

<class 'pandas.core.frame.DataFrame'>
Index: 5609 entries, vyurv213 to da31
Data columns (total 2 columns):
 #   Column    Non-Null Count  Dtype 
---  ------    --------------  ----- 
 0   abstract  5609 non-null   object
 1   keywords  2525 non-null   object
dtypes: object(2)
memory usage: 131.5+ KB


In [7]:
# загружаем список стоп-слов для русского
nltk.download('stopwords')
stop_words = nltk.corpus.stopwords.words('russian')

# примеры стоп-слов
stop_words[:10]

[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\-\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


['и', 'в', 'во', 'не', 'что', 'он', 'на', 'я', 'с', 'со']

In [8]:
# знаки препинания
string.punctuation

'!"#$%&\'()*+,-./:;<=>?@[\\]^_`{|}~'

In [9]:
word_tokenizer = nltk.WordPunctTokenizer()

In [99]:
# dates = [str(x) for x in np.arange(1900, 2022)]


def process_abstractsdb(data):
    texts = []    
    
    # поочередно проходим по всем новостям в списке
    for index,row in data.iterrows():
        # print(row['abstract'])        
        # print(type(row['abstract']))
        text = row['abstract']
        if (row['keywords'] is not None):
            # print(text)
            # print(row['keywords'])
            # print(type(row['keywords']))
            text += row['keywords']                   
        text_lower = text.lower() # приводим все слова к нижнему регистру
        tokens     = word_tokenizer.tokenize(text_lower) #разбиваем екст на слова                
        tokens = [word for word in tokens if (word not in string.punctuation and word not in stop_words and not word.isnumeric())]
                      
        texts.append(tokens) # добавляем в предобработанный список
    
    return texts

In [11]:
abstracts.loc[['vyurv213','vyurv1','vyurv46']].info()

<class 'pandas.core.frame.DataFrame'>
Index: 3 entries, vyurv213 to vyurv46
Data columns (total 2 columns):
 #   Column    Non-Null Count  Dtype 
---  ------    --------------  ----- 
 0   abstract  3 non-null      object
 1   keywords  3 non-null      object
dtypes: object(2)
memory usage: 72.0+ bytes


In [12]:
exp = ["Теперь каждый пример представлен списком слов.",
       "Причем все слова с маленькой буквы.",
       "Пунктуацию и стоп-слова мы удалили."]
texts_exp = process_data(exp)

# texts = process_abstractsdb(abstracts.loc[['vyurv213','vyurv1','vyurv46']])
# texts = process_abstractsdb(abstracts.loc[['vyurv213','vyurv1','vyurv46']])
texts = process_abstractsdb(abstracts)

In [13]:
texts

[['увеличивающийся',
  'рост',
  'числа',
  'компонент',
  'суперкомпьютеров',
  'приводит',
  'специалистов',
  'области',
  'hpc',
  'неблагоприятным',
  'оценкам',
  'будущих',
  'суперкомпьютеров',
  'диапазон',
  'среднего',
  'времени',
  'отказами',
  'составлять',
  'часа',
  'часов',
  'данная',
  'оценка',
  'ставит',
  'вопрос',
  'возможность',
  'проведения',
  'длительных',
  'расчетов',
  'суперкомпьютерах',
  'работе',
  'предлагается',
  'метод',
  'восстановления',
  'отказов',
  'требующий',
  'возврата',
  'большинства',
  'процессов',
  'последней',
  'контрольной',
  'точке',
  'позволить',
  'сократить',
  'накладные',
  'расходы',
  'некоторых',
  'вычислительных',
  'алгоритмов',
  'стандартный',
  'метод',
  'обеспечения',
  'отказоустойчивости',
  'заключается',
  'координированном',
  'сохранении',
  'случае',
  'отказа',
  'осуществляется',
  'возврат',
  'процессов',
  'последней',
  'контрольной',
  'точке',
  'предлагаемая',
  'стратегия',
  'заключается

In [14]:
# инициализируем лемматизатор :)
morph = pymorphy2.MorphAnalyzer()

In [15]:
for aword in texts[2]:
    aword_norm = morph.parse(aword)[0].normal_form
    print("Исходное слово: %s \tЛемматизированное: %s" % (aword, aword_norm))

Исходное слово: рассматриваются 	Лемматизированное: рассматриваться
Исходное слово: вопросы 	Лемматизированное: вопрос
Исходное слово: связанные 	Лемматизированное: связанный
Исходное слово: проведением 	Лемматизированное: проведение
Исходное слово: расчетов 	Лемматизированное: расчёт
Исходное слово: распределенных 	Лемматизированное: распределённый
Исходное слово: вычислительных 	Лемматизированное: вычислительный
Исходное слово: системах 	Лемматизированное: система
Исходное слово: компоненты 	Лемматизированное: компонент
Исходное слово: которых 	Лемматизированное: который
Исходное слово: подвержены 	Лемматизированное: подверженный
Исходное слово: отказам 	Лемматизированное: отказ
Исходное слово: работе 	Лемматизированное: работа
Исходное слово: приводятся 	Лемматизированное: приводиться
Исходное слово: определения 	Лемматизированное: определение
Исходное слово: системы 	Лемматизированное: система
Исходное слово: сбоя 	Лемматизированное: сбой
Исходное слово: ошибки 	Лемматизированное: 

In [16]:
# применяем лемматизацию ко всем текстам
print(range(len(texts)))

for i in tqdm(range(len(texts))):           # tqdm_notebook создает шкалу прогресса :)
    text_lemmatized = [morph.parse(x)[0].normal_form for x in texts[i]] # применяем лемматизацию для каждого слова в тексте
    texts[i] = ' '.join(text_lemmatized)
    # time.sleep(1)  

range(0, 5609)


  0%|          | 0/5609 [00:00<?, ?it/s]

In [17]:
texts

['увеличиваться рост число компонент суперкомпьютер приводить специалист область hpc неблагоприятный оценка будущий суперкомпьютер диапазон среднее время отказ составлять час час дать оценка ставить вопрос возможность проведение длительный расчёт суперкомпьютер работа предлагаться метод восстановление отказ требовать возврат большинство процесс последний контрольный точка позволить сократить накладный расход некоторый вычислительный алгоритм стандартный метод обеспечение отказоустойчивость заключаться координировать сохранение случай отказ осуществляться возврат процесс последний контрольный точка предлагать стратегия заключаться координировать сохранение журналирование передаваемый данные случай отказ происходить асинхронный восстановление асинхронный восстановление несколько запасный процесс проводить пересчёт данные потерянный отказ остальной процесс находиться ожидание окончание процедура восстановление потерянный данные разработать параллельный программа решающий задача распростра

https://stackoverflow.com/questions/46118910/scikit-learn-vectorizer-max-features

In [18]:
# Fit TF-IDF on train texts
# vectorizer = TfidfVectorizer(min_df=1,   max_features=None, strip_accents='unicode',  analyzer='word',token_pattern=r'\w{2,}',ngram_range=(1, 2), use_idf=1,smooth_idf=1,sublinear_tf=1)
vectorizer = TfidfVectorizer(min_df=1,   max_features=None, analyzer='word',token_pattern=r'\w{2,}', use_idf=1,smooth_idf=1,sublinear_tf=1) 
vectorizer.fit(texts)


TfidfVectorizer(smooth_idf=1, sublinear_tf=1, token_pattern='\\w{2,}',
                use_idf=1)

In [19]:
print(len(vectorizer.get_feature_names_out()))


16601


In [20]:

# Топ-10 слов
vectorizer.get_feature_names_out()[:]

array(['00458', '00750', '01625', ..., 'яэу', 'ёмкостный', 'ёмкость'],
      dtype=object)

In [135]:
tf_idf_matrix = vectorizer.fit_transform(texts)

In [136]:
print(type(tf_idf_matrix))

<class 'scipy.sparse._csr.csr_matrix'>


In [137]:
tf_idf_matrix.shape

(5609, 16601)

In [24]:
def save_vectorizer(data,status='write'):
    filename = '../data/vectorizer.pkl'    
    if status == 'write':        
        with open(filename,'wb') as outp:
            pickle.dump(data, outp, pickle.HIGHEST_PROTOCOL)
            
def save_tf_idf_matrix(data,status='write'):
    filename = '../data/tf_idf_matrix.pkl'    
    if status == 'write':        
        with open(filename,'wb') as outp:
            pickle.dump(data, outp, pickle.HIGHEST_PROTOCOL)

In [25]:
# save_vectorizer(vectorizer,status="write")
save_tf_idf_matrix(tf_idf_matrix,status="write")

In [26]:
def load_vectorizer():
    filename = '../data/vectorizer.pkl'
    res = None    
    with open(filename,'rb') as inp:
        res = pickle.load(inp)
    return res

def load_tf_idf_matrix():
    filename = '../data/tf_idf_matrix.pkl'
    res = None    
    with open(filename,'rb') as inp:
        res = pickle.load(inp)
    return res


In [27]:
# x = load_vectorizer()

In [28]:
# x.get_feature_names_out()[:10]

# Importance of the article for Request

In [111]:
def process_request(data):        
    text_lower = data.lower()
    tokens = word_tokenizer.tokenize(text_lower)
    tokens = [word for word in tokens if (word not in string.punctuation and word not in stop_words and not word.isnumeric())]        
    texts = ' '.join(tokens)         
    return [morph.parse(texts)[0].normal_form]

In [163]:
from collections import defaultdict
def get_authors_rating(df, coef):
    # print(df)
    # print(type(df))
    # print(coef)
    # print(type(coef))
    rating = defaultdict(int)
    
    for index in range(len(df)):
        # print(f'index = {index}, row = {df.iloc[index]}')        
        for author in df.iloc[index]['author_id']:  
            # print(index)          
            # print(f'add coef = {coef[index]} to author = {author}')
            rating[author] += coef[index]            
            # print(rating)
    # dict(sorted(rating.items(), key=lambda item: item[1]))
    rating_list = [ (k,v) for k, v in sorted(rating.items(), key=lambda item: item[1], reverse=True)]
    return rating_list

In [164]:

request = 'суперкомпьютерное моделирование отказоустойчивые вычисления на hpc системах'
# request = process_request(request)
# print(request)
# print(type(request))



In [195]:
# result =  get_model_response(request, vectorizer, tf_idf_matrix, abstracts, authors_dict)
def get_model_response(request, vectorizer, tf_idf_matrix, abstracts, authors_dict):
    # tf_idf_matrix= train_X = vectorizer.fit_transform(texts)
    # print(request)
    # print(type(request))
    request = process_request(request)
    # print(request)
    # print(type(request))
    vect_req = vectorizer.transform(request)
    onehot = Binarizer()
    ohe_request = onehot.fit_transform(vect_req.toarray())
    # print(ohe_request.shape)
    # print(tf_idf_matrix.shape)
    coef= tf_idf_matrix.dot(ohe_request.T)
    # print(coef)
    coef = coef.flatten()
    
    
    max_number_of_articles = 30
    low_bound = 0.01
    max_output_pubs = 5
    max_output_authors = 5
    
    pubs_index = np.argsort(coef)[::-1][:max_number_of_articles]
    # print(pubs_index)
    # coef[pubs_index]
    
    low_bound_pub_index  = [ind for ind in pubs_index if coef[ind]>low_bound]
    # print(low_bound_pub_index)
    # print(coef[low_bound_pub_index])
    
    req_pups = list(abstracts.iloc[low_bound_pub_index].index)
    # print(req_pups)
    # print(pub.loc[req_pups].head())
    
    top_pubs = pub.loc[req_pups]['reference']
    
    top_autors = get_authors_rating(pub.loc[req_pups],coef[pubs_index])
    # print(top_autors[:max_output_authors][0], top_autors[:max_output_authors][1])
    # print(type(top_autors))
    # print(top_autors)
    index = 0
    for item in top_autors:
        # print(index, item)        
        if index >= max_output_authors:
            break
        if item[0] in authors_dict:
            index +=1
            print(f'author = {authors_dict[item[0]]}, his raiting = {round(item[1],2)}')
            
            
    for item in top_pubs[:max_output_pubs]:
        print(item)
    # I need to return 
    # pub.loc[req_pups]['reference']

In [196]:
result =  get_model_response(request, vectorizer, tf_idf_matrix, abstracts, authors_dict)

суперкомпьютерное моделирование отказоустойчивые вычисления на hpc системах
<class 'str'>
['суперкомпьютерное моделирование отказоустойчивые вычисления hpc система']
<class 'list'>
(1, 16601)
(5609, 16601)
[[0.10449506]
 [0.19014581]
 [0.07894995]
 ...
 [0.        ]
 [0.        ]
 [0.        ]]
[3047  933 2808   64 2280  927   71 2591 2285 1640   32 4170 5182 3907
 3612 2986  923  924  639  922 4169   96  626 3484  304 4829 2182   10
 2283  129]
[3047, 933, 2808, 64, 2280, 927, 71, 2591, 2285, 1640, 32, 4170, 5182, 3907, 3612, 2986, 923, 924, 639, 922, 4169, 96, 626, 3484, 304, 4829, 2182, 10, 2283, 129]
[0.42011489 0.32770605 0.31603552 0.30864907 0.30818996 0.28419253
 0.28287868 0.27995063 0.27390694 0.26752615 0.2624399  0.25968965
 0.25926605 0.25703925 0.25170887 0.24813309 0.24726933 0.24726933
 0.24717473 0.24664339 0.24274302 0.23957628 0.23917389 0.23843853
 0.23744578 0.23444255 0.23418004 0.23178942 0.23015415 0.2286968 ]
['mm2110', 'ipmp1301', 'mm2285', 'zvmmf10869', 'zvmm

In [160]:
# train_y = vectorizer.transform(request)
# onehot = Binarizer()
# ohe_request = onehot.fit_transform(train_y.toarray())


In [52]:
# print(corpus)
# print(type(corpus))

In [115]:
# print(ohe_request.shape)
# print(train_X.shape)

(1, 16601)
(5609, 16601)


In [116]:
# answer= train_X.dot(ohe_request.T)
# print(answer)

[[0.10449506]
 [0.19014581]
 [0.07894995]
 ...
 [0.        ]
 [0.        ]
 [0.        ]]


In [117]:
# answer = answer.flatten()

In [126]:
# max_number_of_articles = 10
# low_bound = 0.301

In [127]:
# pubs_index = np.argsort(answer)[::-1][:max_number_of_articles]
# print(pubs_index)

[3047  933 2808   64 2280  927   71 2591 2285 1640]


In [128]:
# answer[pubs_index]

array([0.42011489, 0.32770605, 0.31603552, 0.30864907, 0.30818996,
       0.28419253, 0.28287868, 0.27995063, 0.27390694, 0.26752615])

In [129]:
# low_bound_pub_index  = [ind for ind in pubs_index if answer[ind]>low_bound]
# print(low_bound_pub_index)

[3047, 933, 2808, 64, 2280]


In [130]:
# answer[low_bound_pub_index]

array([0.42011489, 0.32770605, 0.31603552, 0.30864907, 0.30818996])

In [131]:
# req_pups = list(abstracts.iloc[low_bound_pub_index].index)
# print(req_pups)

['mm2110', 'ipmp1301', 'mm2285', 'zvmmf10869', 'zvmmf694']


In [132]:

# pub.loc[req_pups]

author_id  \
mm2110      [33303, 33304, 28433, 38733]   
ipmp1301                         [30878]   
mm2285             [26425, 22255, 41166]   
zvmmf10869         [18171, 82237, 31723]   
zvmmf694           [31843, 54255, 38147]   

                                                   doi       udk  \
mm2110                                            None    :519.6   
ipmp1301                                          None      None   
mm2285                                            None      None   
zvmmf10869  :https://doi.org/10.1134/S0044466919030062  :519.635   
zvmmf694                                          None  :519.634   

                                                  send               type  \
mm2110                                      15.01.1992               None   
ipmp1301                                          None           Препринт   
mm2285                                      02.07.1991               None   
zvmmf10869                                  18.07.2018  СтатьяУДК:519.635   
zvmmf694    30.06.2004Исправленный вариант: 30.09.2004  СтатьяУДК:519.634   

                                                    reference  \
mm2110      А. В. Колдоба, Ю. А. Повещенко, П. П. Матус, М...   
ipmp1301    Г. К. Боровин, “Некоторые особенности моделиро...   
mm2285      Ю. Н. Карамзин, В. А. Трофимов, А. Э. Черток, ...   
zvmmf10869  Б. Н. Четверушкин, А. В. Савельев, В. И. Савел...   
zvmmf694    Т. Г. Елизарова, M. Е. Соколова, Ю. В. Шеретов...   

                                                           by  \
mm2110      А.~В.~Колдоба, Ю.~А.~Повещенко, П.~П.~Матус, М...   
ipmp1301                                        Г.~К.~Боровин   
mm2285           Ю.~Н.~Карамзин, В.~А.~Трофимов, А.~Э.~Черток   
zvmmf10869  Б.~Н.~Четверушкин, А.~В.~Савельев, В.~И.~Савельев   
zvmmf694       Т.~Г.~Елизарова, M.~Е.~Соколова, Ю.~В.~Шеретов   

                                                        paper  \
mm2110      Математическое моделирование течения жидкости ...   
ipmp1301    Некоторые особенности моделирования электромех...   
mm2285      Об одном алгоритме численного решения уравнени...   
zvmmf10869  Компактная квазигазодинамическая система для в...   
zvmmf694    Квазигазодинамические уравнения и численное мо...   

                                       jour    yr   vol issue     pages  
mm2110                 Матем. моделирование  1992     4     9    43--54  
ipmp1301    Препринты ИПМ им.~М.~В.~Келдыша  1999  None  None      None  
mm2285                 Матем. моделирование  1991     3    10   95--103  
zvmmf10869  Ж. вычисл. матем. и матем. физ.  2019    59     3  526--533  
zvmmf694    Ж. вычисл. матем. и матем. физ.  2005    45     3  545--556

In [134]:
# res = get_authors_rating(pub.loc[req_pups],answer[pubs_index])
# print(res)

In [62]:
pub.loc[req_pups].head()

author_id   doi  \
mm2110                        [33303, 33304, 28433, 38733]  None   
ipmp178                                            [79679]  None   
qe9901   [21692, 86848, 32827, 90223, 46543, 90980, 328...  None   
mm1201                        [33442, 31603, 31604, 19910]  None   
mm1180                                      [33099, 19910]  None   

                                     udk        send  \
mm2110                            :519.6  15.01.1992   
ipmp178                             None        None   
qe9901   :533.9:621.373.826PACS:52.38.-r  20.04.1987   
mm1201                              None  21.06.2007   
mm1180                              None  30.03.1999   

                                             type  \
mm2110                                       None   
ipmp178                                  Препринт   
qe9901   СтатьяУДК:533.9:621.373.826PACS:52.38.-r   
mm1201                                       None   
mm1180                                       None   

                                                 reference  \
mm2110   А. В. Колдоба, Ю. А. Повещенко, П. П. Матус, М...   
ipmp178  С. А. Махов, “Пятисекторная долгосрочная макро...   
qe9901   Н. Г. Басов, Г. А. Вергунова, П. П. Волосевич,...   
mm1201   Р. В. Жалнин, Н. В. Змитренко, М. Е. Ладонкина...   
mm1180   И. В. Белов, В. Ф. Тишкин, “Высокочастотные эл...   

                                                        by  \
mm2110   А.~В.~Колдоба, Ю.~А.~Повещенко, П.~П.~Матус, М...   
ipmp178                                        С.~А.~Махов   
qe9901                                                None   
mm1201   Р.~В.~Жалнин, Н.~В.~Змитренко, М.~Е.~Ладонкина...   
mm1180                           И.~В.~Белов, В.~Ф.~Тишкин   

                                                     paper  \
mm2110   Математическое моделирование течения жидкости ...   
ipmp178  Пятисекторная долгосрочная макромодель мировой...   
qe9901                                                None   
mm1201   Численное моделирование развития неустойчивост...   
mm1180   Высокочастотные электромагнитные поля внутри п...   

                                    jour    yr   vol issue   pages  
mm2110              Матем. моделирование  1992     4     9  43--54  
ipmp178  Препринты ИПМ им.~М.~В.~Келдыша  2011  None  None    None  
qe9901                              None  None  None  None    None  
mm1201              Матем. моделирование  2007    19    10  61--66  
mm1180              Матем. моделирование  1999    11    11  24--38

In [ ]:
# train_X.todense()[2,[20, 19, 18, 15, 13,  9,  0]].sum()
# train_X.todense()[2,[20, 19, 18, 15, 13,  9,  0]]

In [44]:
absdb.db.loc["mbb374"]

abstract    None
keywords    None
Name: mbb374, dtype: object